# SDC1 Solution example workflow

This notebook contains an example workflow for solving SDC1. Running this workflow on the full set of SDC1 data is resource intensive, requiring ~100GB RAM, though the same process can be run on smaller sample data.

Some sample data can be downloaded into this notebook environment via running the script `bash binder/download_sample_data.sh` in a terminal. By default this places data in `data/sample_images`, which is the directory assumed by this workflow.

In [1]:
import os
from pathlib import Path

import numpy as np
from ska_sdc import Sdc1Scorer
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import classification_report

from ska.sdc1.models.sdc1_image import Sdc1Image
from ska.sdc1.utils.bdsf_utils import cat_df_from_srl_df, load_truth_df
from ska.sdc1.utils.classification import SKLClassification
from ska.sdc1.utils.source_finder import SourceFinder
import pandas


---

In [2]:

# Challenge frequency bands
#
FREQS = [560, 1400, 9200]


# Input data paths; assumes defaults from download_data.sh
#
print("data", "sample_images", "{}mhz_1000h.fits".format(500))
def image_path(freq):
    return os.path.join("data", "sample_images", "{}mhz_1000h.fits".format(freq))


def pb_path(freq):
    return os.path.join("data", "sample_images", "{}mhz_pb.fits".format(freq))


def train_truth_path(freq):
    return os.path.join("/idia/users/hussein/data", "truth", "{}mhz_truth_train.txt".format(freq))


def full_truth_path(freq):
    return os.path.join("/idia/users/hussein/data", "truth", "{}mhz_truth_full.txt".format(freq))


# Output data paths
#
def train_source_df_path(freq):
    return os.path.join("data", "sources", "{}mhz_sources_train.csv".format(freq))


def full_source_df_path(freq):
    return os.path.join("data", "sources", "{}mhz_sources_full.csv".format(freq))


def submission_df_path(freq):
    return os.path.join("data", "sources", "{}mhz_submission.csv".format(freq))


def model_path(freq):
    return os.path.join("data", "models", "{}mhz_classifier.pickle".format(freq))


def score_report_path(freq):
    return os.path.join("data", "score", "{}mhz_score.txt".format(freq))


def write_df_to_disk(df, out_path):
    """ Helper function to write DataFrame df to a file at out_path"""
    out_dir = os.path.dirname(out_path)
    Path(out_dir).mkdir(parents=True, exist_ok=True)
    df.to_csv(out_path, index=False)



data sample_images 500mhz_1000h.fits


In [3]:
"""
Run through a simple analysis workflow to solve SDC1

1) Preprocess images (correct PB) and crop out the training area for
    building ML model
2) Find sources in the PB-corrected training images
3) Train a classifier for each band to predict the class of each source
4) Find sources in the full PB-corrected image
5) Predict the class of each source
6) Calculate the score for each image band, and write out a short report
"""
# 1) Create in-memory representation of image and preprocess
print("\nStep 1: Preprocessing")
sdc1_image_list = []
for freq in FREQS:
    new_image = Sdc1Image(freq, image_path(freq), pb_path(freq))
    new_image.preprocess()
    sdc1_image_list.append(new_image)

# In data/images, we now have PB-corrected and training images for each band




Step 1: Preprocessing


 [astropy.io.fits.verify]
 [astropy.io.fits.verify]
 [astropy.io.fits.verify]


In [4]:

# 2) Source finding (training):
print("\nStep 2: Source finding (train)")
sources_training = {}
for sdc1_image in sdc1_image_list:
    source_finder = SourceFinder(sdc1_image.train)
    sl_df = source_finder.run()
    sources_training[sdc1_image.freq] = sl_df

    # (Optional) Write source list DataFrame to disk
    write_df_to_disk(sl_df, train_source_df_path(sdc1_image.freq))

    # Remove temp files:
    source_finder.reset()

# <Additional feature engineering of the source DataFrames can be performed here>



--> Opened '560mhz_1000h_train.fits'
Image size .............................. : (3471, 3191) pixels
Number of channels ...................... : 1
Number of Stokes parameters ............. : 1
Beam shape (major, minor, pos angle) .... : (4.16667e-04, 4.16667e-04, 0.0) degrees



Step 2: Source finding (train)


Frequency of image ...................... : 560.000 MHz
Number of blank pixels .................. : 0 (0.0%)
Flux from sum of (non-blank) pixels ..... : 0.217 Jy
--> Calculating background rms and mean images
/users/hussein/source/dc1/vdc1/lib/python3.8/site-packages/numpy/core/fromnumeric.py:43: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  result = getattr(asarray(obj), method)(*args, **kwds)
Using user-specified rms_box ............ : (74, 19) pixels
--> Using 2D map for background rms
--> Variation in mean image significant
--> Using 2D map for background mean
Min/max values of background rms map .... : (1.47e-07, 3.54e-06) Jy/beam
Min/max values of background mean map ... : (-5.17e-07, 4.51e-06) Jy/beam
Minimum number of pixels per island ..... : 6
Number of isla

Fitting islands with Gaussians .......... : [|] 0/20248

stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device


...

-Fitting islands with Gaussians .......... : [-] 10/11[-1G

stty: 'standard input': Inappropriate ioctl for device


Fitting islands with Gaussians .......... : [] 11/11[-6GFitting islands with Gaussians .......... : [] 11/11[-6G

stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
Total number of Gaussians fit to image .. : 8
Total flux density in model ............. : 0.000 Jy


stty: 'standard input': Inappropriate ioctl for device
--> Grouping Gaussians into sources
Number of sources formed from Gaussians   : 8
    Island #0 (x=41, y=2799): fit with 1 Gaussian with flag = 256
    Island #4 (x=1225, y=684): fit with 1 Gaussian with flag = 64
    Island #5 (x=2176, y=25): fit with 1 Gaussian with flag = 256
Please check these islands. If they are valid islands and
should be fit, try adjusting the flagging options (use
show_fit with "ch0_flagged=True" to see the flagged Gaussians
and "help 'flagging_opts'" to see the meaning of the flags)
or enabling the wavelet module (with "atrous_do=True").
To include empty islands in output source catalogs, set
incl_empty=True in the write_catalog task.


In [5]:
# 3) Train classifiers for each frequency's source DataFrame:
print("\nStep 3: Training classifiers")
classifiers = {}
for freq, source_train_df in sources_training.items():
    # Load truth catalogue for the training area into memory
    train_truth_cat_df = load_truth_df(train_truth_path(freq), skiprows=18)

    # Construct and train classifier
    classifier = SKLClassification(
        algorithm=RandomForestClassifier,
        classifier_kwargs={"n_estimators": 100, "class_weight": "balanced"},
    )
    srl_df = classifier.train(
        source_train_df, train_truth_cat_df, regressand_col="class_t", freq=freq
    )

    # Store model for prediction later
    classifiers[freq] = classifier

    # (Optional) Write model to disk; allows later loading without retraining.
    model_dir = os.path.dirname(model_path(freq))
    Path(model_dir).mkdir(parents=True, exist_ok=True)
    classifier.save_model(model_path(freq))




Step 3: Training classifiers


In [ ]:
# this one takes long to run
# 4) Source finding (full):
sources_full = {}
print("\nStep 4: Source finding (full)")
for sdc1_image in sdc1_image_list:
    source_finder = SourceFinder(sdc1_image.pb_corr_image)
    sources_full[sdc1_image.freq] = source_finder.run()

    # Remove temp files:
    source_finder.reset()

#this step takes quite some time

--> Opened '560mhz_1000h_pbcor.fits'
Image size .............................. : (5206, 4786) pixels
Number of channels ...................... : 1
Number of Stokes parameters ............. : 1
Beam shape (major, minor, pos angle) .... : (4.16667e-04, 4.16667e-04, 0.0) degrees



Step 4: Source finding (full)


Frequency of image ...................... : 560.000 MHz
Number of blank pixels .................. : 0 (0.0%)
Flux from sum of (non-blank) pixels ..... : 0.930 Jy
--> Calculating background rms and mean images
/users/hussein/source/dc1/vdc1/lib/python3.8/site-packages/numpy/core/fromnumeric.py:43: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  result = getattr(asarray(obj), method)(*args, **kwds)
Using user-specified rms_box ............ : (74, 19) pixels
--> Using 2D map for background rms
--> Variation in mean image not significant
--> Using constant background mean
Min/max values of background rms map .... : (9.66e-08, 3.55e-06) Jy/beam
Value of background mean ................ : -0.0 Jy/beam
Minimum number of pixels per island ..... : 6
Number of islands found .....

Fitting islands with Gaussians .......... : [|] 0/45097

stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device


...

//Fitting islands with Gaussians .......... : [/] 10287/45097Fitting islands with Gaussians .......... : [|] 10286/45097--\Fitting islands with Gaussians .......... : [-] 10288/45097|Fitting islands with Gaussians .......... : [\] 10289/45097/Fitting islands with Gaussians .......... : [/] 10291/45097Fitting islands with Gaussians .......... : [/] 10291/45097\\Fitting islands with Gaussians .......... : [\] 10293/45097Fitting islands with Gaussians .......... : [-] 10292/45097Fitting islands with Gaussians .......... : [-] 10292/45097///Fitting islands with Gaussians .......... : [|] 10294/45097-Fitting islands with Gaussians .......... : [/] 10295/45097\Fitting islands with Gaussians .......... : [\] 10297/45097|Fitting islands with Gaussians .......... : [/] 10300/45097Fitting islands with Gaussians .......... : [\] 10297/45097Fitting islands with Gaussians .......... : [/] 10300/45097/Fitting islands with Gaussians .......... : [/] 10300/45097||Fitting islands with Gaussians .......

stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input'stty: 'standard input': Inappropriate ioctl for device
: Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'sta

Fitting islands with Gaussians .......... : [\] 10318/45097Fitting islands with Gaussians .......... : [\] 10318/45097|||Fitting islands with Gaussians .......... : [|] 10319/45097/-Fitting islands with Gaussians .......... : [/] 10320/45097Fitting islands with Gaussians .......... : [-] 10321/45097\Fitting islands with Gaussians .......... : [|] 10323/45097|Fitting islands with Gaussians .......... : [|] 10323/45097Fitting islands with Gaussians .......... : [|] 10323/45097Fitting islands with Gaussians .......... : [/] 10324/45097/|Fitting islands with Gaussians .......... : [-] 10325/45097||Fitting islands with Gaussians .......... : [\] 10326/45097/-Fitting islands with Gaussians .......... : [|] 10327/45097Fitting islands with Gaussians .......... : [/] 10328/45097Fitting islands with Gaussians .......... : [|] 10331/45097Fitting islands with Gaussians .......... : [|] 10331/45097Fitting islands with Gaussians .......... : [|] 10331/45097/--\\Fitting islands with Gaussians .......

stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'standard input': Inappropriate ioctl for device
stty: 'sta

Fitting islands with Gaussians .......... : [/] 10350/45097Fitting islands with Gaussians .......... : [\] 10351/45097Fitting islands with Gaussians .......... : [|] 10352/45097Fitting islands with Gaussians .......... : [|] 10352/45097Fitting islands with Gaussians .......... : [-] 10350/45097

In [ ]:
# 5) Source classification (full)
print("\nStep 5: Classification")
for freq, source_df in sources_full.items():
    source_df["class"] = classifiers[freq].test(source_df)
    class_prob = classifiers[freq].predict_proba(source_df)
    source_df["class_prob"] = np.amax(class_prob, axis=1)

    # (Optional) Write source list DataFrame to disk
    write_df_to_disk(source_df, full_source_df_path(freq))



In [ ]:
# 6) Create final catalogues and calculate scores
print("\nStep 6: Final score")
for freq, source_df in sources_full.items():
    # Assemble submission and truth catalogues for scoring
    sub_cat_df = cat_df_from_srl_df(source_df, guess_class=False)
    truth_cat_df = load_truth_df(full_truth_path(freq), skiprows=0)

    # (Optional) Write final submission catalogue to disk
    write_df_to_disk(sub_cat_df, submission_df_path(freq))

    # Calculate score
    scorer = Sdc1Scorer(sub_cat_df, truth_cat_df, freq)
    score = scorer.run(mode=0, train=False, detail=True)

    # Write short score report:
    score_path = score_report_path(freq)
    score_dir = os.path.dirname(score_path)
    Path(score_dir).mkdir(parents=True, exist_ok=True)

    with open(score_path, "w+") as report:
        report.write(
            "Image: {}, frequency: {} MHz\n".format(image_path(freq), freq)
        )
        report.write("Score was {}\n".format(score.value))
        report.write("Number of detections {}\n".format(score.n_det))
        report.write("Number of matches {}\n".format(score.n_match))
        report.write(
            "Number of matches too far from truth {}\n".format(score.n_bad)
        )
        report.write("Number of false detections {}\n".format(score.n_false))
        report.write("Score for all matches {}\n".format(score.score_det))
        report.write("Accuracy percentage {}\n".format(score.acc_pc))
        report.write("Classification report: \n")
        report.write(
            classification_report(
                score.match_df["class_t"],
                score.match_df["class"],
                labels=[1, 2, 3],
                target_names=["1 (SS-AGN)", "2 (FS-AGN)", "3 (SFG)"],
                digits=4,
            )
        )

print("\nComplete")

In [9]:
print(1)

1
